# Universe Simulation 2: Eulerian Continuums

## Background Math
### General continuity equation

- https://en.wikipedia.org/wiki/Continuum_mechanics#Balance_laws
- https://en.wikipedia.org/wiki/Continuity_equation#Differential_form

$$ \frac{\partial \rho}{\partial t} = - \vec{\nabla} \cdot \vec{j} + s $$

### Conservation of mass

$$ \frac {\partial \rho }{\partial t} = - \vec{\nabla} \cdot \left( \rho \vec{v} \right) $$

$$ \frac {\partial \rho }{\partial t} = \sum_{j} \frac{\partial}{\partial x_{j}} \left( \rho v_{j} \right) $$

### Conservation of momentum

- https://en.wikipedia.org/wiki/Cauchy_momentum_equation
- https://en.wikipedia.org/wiki/Navier%E2%80%93Stokes_equations
- https://en.wikipedia.org/wiki/Derivation_of_the_Navier%E2%80%93Stokes_equations
- https://en.wikipedia.org/wiki/Viscosity#Momentum_transport
- https://en.wikipedia.org/wiki/Viscous_stress_tensor

inviscid
$$ \frac {\partial}{\partial t} \left( \rho \vec{v} \right) = - \vec{\nabla} \cdot \left( \rho \vec{v} \otimes \vec{v} \right) + \vec{f} $$

$$ \frac {\partial}{\partial t} \left( \rho v_{i} \right) = - \sum_{j} \frac{\partial}{\partial x_{j}} \left( \rho v_{i} v_{j} \right) + f_{i} $$

viscosity (stresses of momentum diffusion)
$$ \tau_{ij} = \sum_{kl} \mu_{ijkl} \frac{\partial}{\partial x_{l}} v_{k} $$

Putting these together

$$ \frac {\partial}{\partial t} \left( \rho v_{i} \right) = - \sum_{j} \frac{\partial}{\partial x_{j}} \left( \rho v_{i} v_{j} + \tau_{ij} \right) + f_{i} $$


### Conservation of energy

- https://en.wikipedia.org/wiki/Heat_equation
- https://en.wikipedia.org/wiki/Internal_energy
- https://en.wikipedia.org/wiki/Clausius%E2%80%93Duhem_inequality

$$ \frac{\partial u}{\partial t} = - \vec{\nabla} \cdot \vec{q} + s $$

Fourier's law of heat conduction (diffusion)
- https://en.wikipedia.org/wiki/Thermal_conduction#Fourier's_law
$$ \vec{q} = -k \vec{\nabla} T $$

Heat capacity
- https://en.wikipedia.org/wiki/Specific_heat_capacity
- https://en.wikipedia.org/wiki/Equation_of_state#Classical_ideal_gas_law
$$ C_{V} = \frac{f}{2} \frac{N_{A}}{M} k_{B}$$

$$ \rho C_{V} = \frac{\mathrm{d} u}{\mathrm{d} T} $$

Putting these together

$$ \frac{\partial u}{\partial t} = \vec{\nabla} \cdot \left( \frac{k}{\rho C_{V}} \vec{\nabla} u \right) + s $$

$$ \frac{\partial u}{\partial t} = \frac{k}{\rho C_{V}} \nabla^{2} u + s $$


### PDEs
- https://en.wikipedia.org/wiki/Crank%E2%80%93Nicolson_method#Crank%E2%80%93Nicolson_for_nonlinear_problems
- https://en.wikipedia.org/wiki/MacCormack_method
- https://en.wikipedia.org/wiki/Finite_difference_coefficient
- https://en.wikipedia.org/wiki/Total_variation_diminishing
- https://en.wikipedia.org/wiki/Flux_limiter
- https://en.wikipedia.org/wiki/MUSCL_scheme

#### Stam's Stable Fluids
- https://www.youtube.com/watch?v=iKAVRgIrUOU
- https://developer.nvidia.com/gpugems/gpugems/part-vi-beyond-triangles/chapter-38-fast-fluid-dynamics-simulation-gpu
- https://pages.cs.wisc.edu/~chaol/data/cs777/stam-stable_fluids.pdf

### Additional
- https://en.wikipedia.org/wiki/Euler_equations_(fluid_dynamics)
- https://en.wikipedia.org/wiki/Clausius%E2%80%93Duhem_inequality
- https://en.wikipedia.org/wiki/Burgers%27_equation
- https://github.com/pmocz/finitevolume-python
- https://docs.scipy.org/doc/scipy/reference/generated/scipy.ndimage.convolve.html
- https://docs.scipy.org/doc/scipy/reference/generated/scipy.integrate.solve_ivp.html#scipy.integrate.solve_ivp
- https://en.wikipedia.org/wiki/Viscoelasticity

In [1]:
import numpy as np

In [8]:
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation

from IPython.display import HTML

In [2]:
import scipy.ndimage
import scipy.linalg

In [590]:
class EulerianContinuum:
    def __init__(self, dt=0.01, relax=0.01, steps=100, n=[1], x=((0,1),), u=[0], u_bc='wrap', thermal_conductivity=1, v=[[0]], v_bc='wrap', viscosity=1):
        self.relax = relax
        self.steps = steps
        
        self.n = tuple(n)
        self.dim = len(n)
        self.x = x
        self.dx = tuple([(jr-jl)/(jn-1) for jn,(jl,jr) in zip(self.n, self.x)])
        
        self.dt = dt
        self.u0 = np.array(u, dtype='double')
        self.v0 = np.array(v, dtype='double')
        
        self.u_bc = u_bc
        self.v_bc = v_bc
        
        self.thermal_conductivity = thermal_conductivity
        self.viscosity = viscosity
        
        self.reset()
    
    
    def reset(self):
        self.t = 0
        self.u = self.apply_boundaries(self.u0.copy(), 0)
        self.v = self.v0.copy()
    
        
    def diff_kernel(self, idim):
        diff_kernel = np.zeros((3,)*self.dim, dtype='double')
        # left
        idx = [1] * self.dim
        idx[idim] = 0
        diff_kernel[*idx] = -1 / self.dx[idim] / 2
        # right
        idx = [1] * self.dim
        idx[idim] = 2
        diff_kernel[*idx] = 1 / self.dx[idim] / 2
        return diff_kernel
    
        
    def second_diff_kernel(self, idim):
        diff_kernel = np.zeros((3,)*self.dim, dtype='double')
        # left
        idx = [1] * self.dim
        idx[idim] = 0
        diff_kernel[*idx] = 1 / self.dx[idim]**2
        # right
        idx = [1] * self.dim
        idx[idim] = 2
        diff_kernel[*idx] = 1 / self.dx[idim]**2
        # center
        idx = [1] * self.dim
        diff_kernel[*idx] = -2 / self.dx[idim]**2
        return diff_kernel
    
    
    def laplacian_kernel(self):
        laplacian_kernel = np.zeros((3,)*self.dim, dtype='double')
        laplacian_kernel[(1,)*self.dim] = -2*self.dim / self.dx[0]**2
        for idim in range(self.dim):
            # left
            idx = [1] * self.dim
            idx[idim] = 0
            laplacian_kernel[*idx] = 1 / self.dx[idim]**2
            # right
            idx = [1] * self.dim
            idx[idim] = 2
            laplacian_kernel[*idx] = 1 / self.dx[idim]**2
        return laplacian_kernel
    
    
    def laplacian(self, scalar_field):
        laplacian = scipy.ndimage.convolve(scalar_field, self.laplacian_kernel(), mode='wrap')
        if self.u_bc == 'wrap':
            return laplacian
        return laplacian
    
    
    def divergence(self, vector_field):
        return sum(
            scipy.ndimage.convolve(
                vector_field[::,idim], 
                self.diff_kernel(idim).reshape((3,)*self.dim + (1,)), 
                mode='wrap'
            )
            for idim in range(self.dim)
        )

    
    def vector_advection(self, vector_field):
        vector_flux = self.v.reshape((*self.n, self.dim, 1)) * vector_field.reshape((*self.n, 1, self.dim))
        return sum(
            scipy.ndimage.convolve(vector_flux[::,idim], self.diff_kernel(idim).reshape((3,)*self.dim + (1,)), mode='wrap')
            for idim in range(self.dim)
        )
    
    def viscosity_v(self, v):
        return self.viscosity * np.stack([
            scipy.ndimage.convolve(v[::,idim], self.second_diff_kernel(idim), mode='wrap')
            for idim in range(self.dim)
        ], axis=-1)
    
    
    def u_F(self, u):
        F = self.thermal_conductivity * self.laplacian(u)
        return F
    
    
    def v_F(self, v):
        advection = self.vector_advection(v)
        viscosity = self.viscosity_v(v)
        return advection + viscosity
    
    
    def apply_boundaries(self, u, bc):
        # wrapped boundaries
        if bc == 'wrap':
            return u
        # fixed boundaries
        for idim in range(self.dim):
            axes = list(u.shape)
            axes[idim] = 1
            indices = np.indices(axes)
            # left
            indices[0,::] = 0 # here we could vary to create differences
            u[*indices] = bc
            # right
            indices[0,::] = -1
            u[*indices] = bc
        return u
    
    
    def dt_CFL(self):
        #https://en.wikipedia.org/wiki/Courant%E2%80%93Friedrichs%E2%80%93Lewy_condition
        if np.sum(np.abs(self.v)) == 0:
            return self.dt
        return np.min(np.sum(np.array(self.dx) / np.abs(self.v), axis=-1)) * 0.4 # technically 1 should work
    
    
    def step(self):
        dt = min(self.dt, self.dt_CFL())
        
        vnew = self.v
        unew = self.u
        for _ in range(self.steps):
            vnew = (1-self.relax) * vnew + self.relax * (self.v + dt * (self.v_F(self.v) + self.v_F(vnew)) / 2)
            vnew = self.apply_boundaries(vnew, self.v_bc)
            unew = (1-self.relax) *  unew + self.relax * (self.u + dt * (self.u_F(self.u) + self.u_F(unew)) / 2)
            unew = self.apply_boundaries(unew, self.u_bc)
        self.v = vnew
        self.u = unew
          
        self.t += dt
        return

    
    def to(self, tf):
        while self.t < tf:
            self.step()
        
        
    def energy(self):
        return self.u.sum() * np.prod(sim.dx)

## Burgers' Equation

In [633]:
n = [101]
x = ((-1, 1),)
x_vec = np.linspace(*x[0], *n)
v = np.exp(-4*x_vec**2)[::,np.newaxis]/4  # Gaussian initial condition
u = np.zeros(*n, dtype='double')
nu = 0.01

sim = EulerianContinuum(dt=0.01, n=n, x=x, u=u, v=v, viscosity=nu)

In [634]:
sim.reset()
tf = 5
fps = 30


fig, ax = plt.subplots()
ax.set_xlim(*sim.x[0])
ax.set_ylim(-0.1, 0.5)

v_plot, = ax.plot(x_vec, sim.v)

def update(frame):
    sim.to(frame/float(fps))
    v_plot.set_data(x_vec, sim.v)

plt.close(fig)
ani = FuncAnimation(fig, update, frames=int(tf*fps), interval=1000//fps)
HTML(ani.to_jshtml())

## Heat Equation

In [627]:
k = 0.2

n = [101]
x = ((-1, 1),)
x_vec = np.linspace(*x[0], *n)
u = np.exp(-4*x_vec**2)/4  # Gaussian initial condition

u = (x_vec > 0) * 0.4

v = np.zeros((*n,len(n)), dtype='double')

sim = EulerianContinuum(dt=0.01, n=n, x=x, u=u, v=v, u_bc=0, thermal_conductivity=k)

In [628]:
sim.reset()
tf = 4
fps = 30


fig, ax = plt.subplots()
ax.set_xlim(*sim.x[0])
ax.set_ylim(-0.1, 0.5)

u_plot, = ax.plot(x_vec, sim.u)

def update(frame):
    sim.to(frame/float(fps))
    u_plot.set_data(x_vec, sim.u)

plt.close(fig)
ani = FuncAnimation(fig, update, frames=int(tf*fps), interval=1000//fps)
HTML(ani.to_jshtml())